In [2]:
pip install plotly

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install nbformat

Note: you may need to restart the kernel to use updated packages.


In [4]:
# -*- coding: utf-8 -*-
"""
Interaktive Deutschlandkarte mit Plotly:
- liest Brücken-CSV
- liest Landkreise-GeoJSON
- weist Brücken Landkreisen zu (räumlich + Name-Fallback)
- berechnet mittlere Zustandsnote pro Landkreis
- rendert eine interaktive Choropleth-Karte mit Plotly

Dateien, die du anpassen kannst:
- data/bridge_statistic_germany.csv       (oder deine gefüllte CSV)
- landkreise_simplify200.geojson         (Landkreise)
"""

import re
import json
import unicodedata
from pathlib import Path

import pandas as pd
import geopandas as gpd
from shapely.geometry import Point

import plotly.express as px
import plotly.io as pio

# Falls du nicht im Notebook bist, lieber im Browser rendern:
# pio.renderers.default = "browser"

# === Dateien ===
csv_path  = Path("data/bridge_statistic_germany.csv")      # deine Brücken-CSV
# csv_path  = Path("data/filled_bridge_statistic_germany.csv")
geo_path  = Path("landkreise_simplify200.geojson")         # Landkreise-GeoJSON
out_csv   = Path("kreise_zustandsnote_mittel.csv")
out_html  = Path("deutschland_zustand_interaktiv.html")

# === 1) Landkreise laden ===
gdf_kreise = gpd.read_file(geo_path)

def pick_first(cols, candidates):
    for c in candidates:
        if c in cols:
            return c
    return None

colsK = gdf_kreise.columns
col_name = pick_first(colsK, ["GEN", "NAME_3", "NAME", "GEN_NAME", "KREIS"])
col_ags  = pick_first(colsK, ["AGS", "AGS_0", "RS", "RS_0", "ID_3"])
col_sn_l = pick_first(colsK, ["SN_L"])  # Bundesland-Schlüssel, falls vorhanden

if col_name is None:
    raise ValueError(
        f"Konnte keinen Kreisnamen finden. Vorhandene Spalten: {list(colsK)}"
    )

# CRS vereinheitlichen (WGS84 / EPSG:4326)
if gdf_kreise.crs is None:
    gdf_kreise = gdf_kreise.set_crs(4326)
else:
    gdf_kreise = gdf_kreise.to_crs(4326)

# === 2) Brücken-CSV laden (deutsches Format) ===
df = pd.read_csv(csv_path, sep=";", decimal=",", dtype=str, keep_default_na=False)

# sicherstellen, dass diese Spalten existieren
for sp in ["Zustandsnote", "x2", "y2", "X", "Y", "Kreis"]:
    if sp not in df.columns:
        df[sp] = ""

# Zustandsnote numerisch
df["Zustandsnote"] = pd.to_numeric(
    df["Zustandsnote"].str.replace(",", ".", regex=False),
    errors="coerce"
)

# === 3) Punkte erzeugen (bevorzugt x2/y2 in WGS84) ===
def make_points_from_lonlat(dfin, lon_col="x2", lat_col="y2"):
    lon = pd.to_numeric(
        dfin[lon_col].str.replace(",", ".", regex=False),
        errors="coerce"
    )
    lat = pd.to_numeric(
        dfin[lat_col].str.replace(",", ".", regex=False),
        errors="coerce"
    )
    ok = lon.notna() & lat.notna()
    g = gpd.GeoDataFrame(
        dfin[ok].copy(),
        geometry=[Point(xy) for xy in zip(lon[ok], lat[ok])],
        crs=4326
    )
    return g

def make_points_from_utm(dfin, x_col="X", y_col="Y", epsg=25832):
    xx = pd.to_numeric(
        dfin[x_col].str.replace(",", ".", regex=False),
        errors="coerce"
    )
    yy = pd.to_numeric(
        dfin[y_col].str.replace(",", ".", regex=False),
        errors="coerce"
    )
    ok = xx.notna() & yy.notna()
    g = gpd.GeoDataFrame(
        dfin[ok].copy(),
        geometry=[Point(xy) for xy in zip(xx[ok], yy[ok])],
        crs=epsg
    ).to_crs(4326)
    return g

gdf_pts = make_points_from_lonlat(df, "x2", "y2")
used_coords = "WGS84 (x2/y2)"
if len(gdf_pts) == 0:
    gdf_pts = make_points_from_utm(df, "X", "Y", epsg=25832)
    used_coords = "UTM32 (EPSG:25832)"

spatial_join_ok = len(gdf_pts) > 0

# === 4) Räumlicher Join (wenn Punkte vorhanden) ===
if spatial_join_ok:
    joined = gpd.sjoin(
        gdf_pts,
        gdf_kreise[[col_name, col_ags, "geometry"]],
        how="left",
        predicate="within"
    )
else:
    joined = None

# === 5) Fallback-Namensabgleich OHNE unidecode ===
def norm_name(s: str) -> str:
    s = str(s).strip().lower()
    s = s.replace("ä", "ae").replace("ö", "oe").replace("ü", "ue").replace("ß", "ss")
    s = unicodedata.normalize("NFKD", s).encode("ascii", "ignore").decode("ascii")
    s = re.sub(r"\b(landkreis|kreisfreie stadt|kreis|stadt|region|lkr\.?)\b", "", s)
    s = re.sub(r"\s+", " ", s)
    return s.strip()

kreise_names = gdf_kreise[[col_name]].copy()
kreise_names["__kreis_norm__"] = kreise_names[col_name].map(norm_name)

if spatial_join_ok:
    base = joined
else:
    base = df.copy()

base["__br_kreis_norm__"] = base["Kreis"].map(norm_name)

name_map = dict(zip(kreise_names["__kreis_norm__"], gdf_kreise[col_name]))
map_series = base["__br_kreis_norm__"].map(name_map)

if spatial_join_ok:
    if col_name in base.columns:
        base[col_name] = base[col_name].fillna(map_series)
    else:
        base[col_name] = map_series
else:
    base[col_name] = map_series

# === 6) Aggregation pro Landkreis ===
agg = (
    base
    .dropna(subset=["Zustandsnote", col_name])
    .groupby(col_name, as_index=False)
    .agg(
        n_bridges=("Zustandsnote", "size"),
        mean_zust=("Zustandsnote", "mean"),
        median_zust=("Zustandsnote", "median"),
    )
)

if col_ags is not None:
    kreise_keys = gdf_kreise[[col_name, col_ags]].drop_duplicates()
    agg = agg.merge(kreise_keys, on=col_name, how="left")
    agg = (
        agg[["AGS", col_name, "n_bridges", "mean_zust", "median_zust"]]
        .rename(columns={col_name: "NAME"})
    )
else:
    agg = (
        agg[[col_name, "n_bridges", "mean_zust", "median_zust"]]
        .rename(columns={col_name: "NAME"})
    )

agg = agg.sort_values("NAME").reset_index(drop=True)

# Optional: CSV ausgeben, falls du die Tabelle brauchst
# agg.to_csv(out_csv, index=False, encoding="utf-8")
# print(f"[OK] CSV geschrieben: {out_csv.resolve()}")

# === 7) Choropleth-GeoDataFrame bauen ===
gplot = gdf_kreise.merge(agg, left_on=col_name, right_on="NAME", how="left")

# Eindeutige ID-Spalte für GeoJSON / Plotly
id_col = None
if col_ags is not None:
    # Kandidaten: Originalname und _x / _y nach dem Merge
    for c in [col_ags, f"{col_ags}_x", f"{col_ags}_y"]:
        if c in gplot.columns:
            id_col = c
            break

if id_col is not None:
    gplot["id"] = gplot[id_col].astype(str)
else:
    # Fallback: Name als ID (nicht perfekt, aber funktioniert)
    gplot["id"] = gplot["NAME"].astype(str)


# GeoJSON nur mit id + geometry (ohne Timestamp-Spalten)
gplot_json = gplot[["id", "geometry"]].copy()
geojson = json.loads(gplot_json.to_json())

# === 8) Interaktive Plotly-Choropleth-Karte ===
fig = px.choropleth(
    gplot,
    geojson=geojson,
    locations="id",                # Spalte in gplot
    featureidkey="properties.id",  # Schlüssel im GeoJSON
    color="mean_zust",             # Färbung: mittlere Zustandsnote
    hover_name="NAME",
    hover_data={
        "n_bridges": True,
        "mean_zust": ":.2f",
        "median_zust": ":.2f",
    },
    color_continuous_scale="RdYlGn_r",   # grün-gelb-rot (invertiert)
    # OPTIONAL: Skala fest von 1 bis 4, wenn du das möchtest:
    # range_color=(1, 4),
    labels={"mean_zust": "Ø Zustandsnote"},
)

# Deutschland passend zoomen & Achsen ausblenden
fig.update_geos(
    fitbounds="locations",      # auf Deutschland zoomen
    visible=False,              # Achsen ausblenden
    projection_type="mercator", # Standard, aber explizit
    center=dict(lat=51, lon=10),
    projection_scale=7          # höher = näher ran (experimentier: 5–10)
)


fig.update_layout(
    title=(
        "Mittlere Zustandsnote pro Landkreis<br>"
        f"<sup>Zuordnung: {used_coords if spatial_join_ok else 'Name-Match'}</sup>"
    ),
    margin={"r": 0, "t": 60, "l": 0, "b": 0}
)
out_html = "deutschland_zustand_interaktiv.html"

fig.write_html(out_html, include_plotlyjs="cdn")
print("Gespeichert als:", out_html)

# === 9) Plot anzeigen & optional speichern ===
fig.show()

# Optional: als HTML speichern (z. B. für Moodle / ILIAS / Website)
# fig.write_html(out_html, include_plotlyjs="cdn")
# print(f"[OK] Interaktive Karte gespeichert: {out_html.resolve()}")


Gespeichert als: deutschland_zustand_interaktiv.html


In [7]:
pip install dash plotly geopandas pandas shapely pyproj


Note: you may need to restart the kernel to use updated packages.


In [9]:
# -*- coding: utf-8 -*-
"""
Interaktive Deutschlandkarte mit Seitenmenü (Dash)

- links: Checkbox-Menü (Ebenen, Baustoffklasse, Baujahr, Straßenart, Flächenanzeige)
- rechts: Plotly-Karte
- Brücken werden nur angezeigt, wenn sie ALLE gewählten Filter erfüllen
  (Baustoffklasse UND Baujahr-Range UND Straßenart).
- Choropleth-Fläche kann wahlweise Ø Zustandsnote, Ø Traglastindex oder Ø Alter anzeigen.

Starten:
    python bruecken_app.py
und dann im Browser:
    http://127.0.0.1:8050
"""

import re
import json
import unicodedata
from pathlib import Path

import pandas as pd
import geopandas as gpd
from shapely.geometry import Point

import plotly.graph_objects as go

import dash
from dash import dcc, html
from dash.dependencies import Input, Output

# --------------------------------------------------------------------
# 0) Pfade
# --------------------------------------------------------------------
csv_path  = Path("data/bridge_statistic_germany.csv")
geo_path  = Path("landkreise_simplify200.geojson")
states_path = Path("bundeslaender_simplify0.geojson")

# Referenzjahr für Altersberechnung (kannst du anpassen)
AGE_REF_YEAR = 2025

# --------------------------------------------------------------------
# 1) Landkreise & Bundesländer laden
# --------------------------------------------------------------------
gdf_kreise = gpd.read_file(geo_path)

def pick_first(cols, candidates):
    for c in candidates:
        if c in cols:
            return c
    return None

colsK   = gdf_kreise.columns
col_name = pick_first(colsK, ["GEN", "NAME_3", "NAME", "GEN_NAME", "KREIS"])
col_ags  = pick_first(colsK, ["AGS", "AGS_0", "RS", "RS_0", "ID_3"])

if col_name is None:
    raise ValueError(f"Konnte keinen Kreisnamen finden. Spalten: {list(colsK)}")

# CRS vereinheitlichen (WGS84)
if gdf_kreise.crs is None:
    gdf_kreise = gdf_kreise.set_crs(4326)
else:
    gdf_kreise = gdf_kreise.to_crs(4326)

# Bundesländer
gdf_states = gpd.read_file(states_path)
if gdf_states.crs is None:
    gdf_states = gdf_states.set_crs(4326)
else:
    gdf_states = gdf_states.to_crs(4326)

colsS = gdf_states.columns
state_name_col = pick_first(colsS, ["GEN", "NAME", "STATE_NAME"])
state_id_col   = pick_first(colsS, ["RS", "RS_0", "AGS", "AGS_0", "ID"])
if state_id_col is None:
    state_id_col = state_name_col
gdf_states["state_id"] = gdf_states[state_id_col].astype(str)


# --------------------------------------------------------------------
# 2) Brücken laden & Punkte erzeugen
# --------------------------------------------------------------------
df = pd.read_csv(csv_path, sep=";", decimal=",", dtype=str, keep_default_na=False)

for sp in ["Zustandsnote", "x2", "y2", "X", "Y", "Kreis", "Baujahr Überbau", "Traglastindex"]:
    if sp not in df.columns:
        df[sp] = ""

# Zustandsnote numerisch
df["Zustandsnote"] = pd.to_numeric(
    df["Zustandsnote"].str.replace(",", ".", regex=False),
    errors="coerce"
)

# Baujahr Überbau numerisch
df["Baujahr Überbau"] = pd.to_numeric(
    df["Baujahr Überbau"].str.replace(",", ".", regex=False),
    errors="coerce"
)

def make_points_from_lonlat(dfin, lon_col="x2", lat_col="y2"):
    lon = pd.to_numeric(dfin[lon_col].str.replace(",", ".", regex=False), errors="coerce")
    lat = pd.to_numeric(dfin[lat_col].str.replace(",", ".", regex=False), errors="coerce")
    ok = lon.notna() & lat.notna()
    g = gpd.GeoDataFrame(
        dfin[ok].copy(),
        geometry=[Point(xy) for xy in zip(lon[ok], lat[ok])],
        crs=4326,
    )
    return g

def make_points_from_utm(dfin, x_col="X", y_col="Y", epsg=25832):
    xx = pd.to_numeric(dfin[x_col].str.replace(",", ".", regex=False), errors="coerce")
    yy = pd.to_numeric(dfin[y_col].str.replace(",", ".", regex=False), errors="coerce")
    ok = xx.notna() & yy.notna()
    g = gpd.GeoDataFrame(
        dfin[ok].copy(),
        geometry=[Point(xy) for xy in zip(xx[ok], yy[ok])],
        crs=epsg,
    ).to_crs(4326)
    return g

# bevorzugt WGS84 (x2/y2), sonst UTM
gdf_pts = make_points_from_lonlat(df, "x2", "y2")
used_coords = "WGS84 (x2/y2)"
if len(gdf_pts) == 0:
    gdf_pts = make_points_from_utm(df, "X", "Y", epsg=25832)
    used_coords = "UTM32 (EPSG:25832)"

gdf_pts["lon"] = gdf_pts.geometry.x
gdf_pts["lat"] = gdf_pts.geometry.y

# Baujahr in Punkte übernehmen (für Filter)
gdf_pts["Baujahr"] = pd.to_numeric(gdf_pts["Baujahr Überbau"], errors="coerce")

# räumlicher Join (wie im statischen Skript)
spatial_join_ok = len(gdf_pts) > 0
if spatial_join_ok:
    joined = gpd.sjoin(
        gdf_pts,
        gdf_kreise[[col_name, col_ags, "geometry"]],
        how="left",
        predicate="within",
    )
else:
    joined = None


# --------------------------------------------------------------------
# 3) Kreis-Aggregation (für Choropleth) – inkl. Traglastindex & Alter
# --------------------------------------------------------------------
def norm_name(s: str) -> str:
    s = str(s).strip().lower()
    s = s.replace("ä", "ae").replace("ö", "oe").replace("ü", "ue").replace("ß", "ss")
    s = unicodedata.normalize("NFKD", s).encode("ascii", "ignore").decode("ascii")
    s = re.sub(r"\b(landkreis|kreisfreie stadt|kreis|stadt|region|lkr\.?)\b", "", s)
    s = re.sub(r"\s+", " ", s)
    return s.strip()

kreise_names = gdf_kreise[[col_name]].copy()
kreise_names["__kreis_norm__"] = kreise_names[col_name].map(norm_name)

# Basis-DataFrame: zuerst räumlicher Join, sonst Roh-CSV
if spatial_join_ok:
    base = joined
else:
    base = df.copy()

base["__br_kreis_norm__"] = base["Kreis"].map(norm_name)

name_map   = dict(zip(kreise_names["__kreis_norm__"], gdf_kreise[col_name]))
map_series = base["__br_kreis_norm__"].map(name_map)

if spatial_join_ok:
    if col_name in base.columns:
        base[col_name] = base[col_name].fillna(map_series)
    else:
        base[col_name] = map_series
else:
    base[col_name] = map_series

# Traglastindex (römische Ziffern -> 1–5)
roman_map = {
    "I": 1,
    "II": 2,
    "III": 3,
    "IV": 4,
    "V": 5,
}
base["Traglastindex_norm"] = (
    base["Traglastindex"]
    .astype(str)
    .str.upper()
    .str.strip()
    .map(roman_map)
)

# Alter des Überbaus (in Jahren; kann NaN sein, wenn Baujahr fehlt)
base["Alter_Überbau"] = AGE_REF_YEAR - base["Baujahr Überbau"]

agg = (
    base
    .dropna(subset=["Zustandsnote", col_name])
    .groupby(col_name, as_index=False)
    .agg(
        n_bridges=("Zustandsnote", "size"),
        mean_zust=("Zustandsnote", "mean"),
        mean_trag=("Traglastindex_norm", "mean"),
        mean_age=("Alter_Überbau", "mean"),
        median_zust=("Zustandsnote", "median"),
    )
)

if col_ags is not None:
    kreise_keys = gdf_kreise[[col_name, col_ags]].drop_duplicates()
    agg = agg.merge(kreise_keys, on=col_name, how="left")
    agg = agg[[col_ags, col_name, "n_bridges", "mean_zust", "mean_trag", "mean_age", "median_zust"]].rename(
        columns={col_name: "NAME"}
    )
else:
    agg = agg[[col_name, "n_bridges", "mean_zust", "mean_trag", "mean_age", "median_zust"]].rename(
        columns={col_name: "NAME"}
    )

agg = agg.sort_values("NAME").reset_index(drop=True)

gplot = gdf_kreise.merge(agg, left_on=col_name, right_on="NAME", how="left")

id_col = None
if col_ags is not None:
    for c in [col_ags, f"{col_ags}_x", f"{col_ags}_y"]:
        if c in gplot.columns:
            id_col = c
            break
if id_col is not None:
    gplot["id"] = gplot[id_col].astype(str)
else:
    gplot["id"] = gplot["NAME"].astype(str)

gplot_json = gplot[["id", "geometry"]].copy()
geojson_kreise = json.loads(gplot_json.to_json())

states_json = gdf_states[["state_id", "geometry"]].copy()
geojson_states = json.loads(states_json.to_json())

germany_outline = gdf_states.dissolve().reset_index(drop=True)
germany_outline["id"] = "germany_outline"
outline_json = json.loads(germany_outline[["id", "geometry"]].to_json())


# --------------------------------------------------------------------
# 4) Brücken-Attribute vorbereiten (Baustoff, Baujahr, Straßenart)
# --------------------------------------------------------------------
zust = pd.to_numeric(gdf_pts["Zustandsnote"], errors="coerce")

# Straßenart-Mapping
mapping_strasse = {
    "E": "Bundesstraße",
    "O": "Bundesstraße",
    "U": "Autobahn",
}
strassen_roh = gdf_pts["Jahresstatistik Lage vereinfacht"].astype(str)
gdf_pts["StraßenartLabel"] = strassen_roh.map(lambda x: mapping_strasse.get(x, x))

# Hover-Text
gdf_pts["hover"] = (
    "<b>" + gdf_pts["Bauwerksname"].astype(str) + "</b><br>"
    "Zustandsnote: " + zust.round(2).astype(str) + "<br>"
    "Baustoffklasse: " + gdf_pts["Baustoffklasse"].astype(str) + "<br>"
    "Baujahr Überbau: " + gdf_pts["Baujahr Überbau"].astype(str) + "<br>"
    "Straßenart: " + gdf_pts["StraßenartLabel"].astype(str)
)

# Ebenen-Checkbox
layer_options = [
    {"label": "Umriss",                        "value": "outline"},
    {"label": "Bundesländer",                  "value": "states"},
    {"label": "Zustand / Traglast / Alter",    "value": "choropleth"},
    {"label": "Landkreis-Grenzen",             "value": "kreise"},
]

# Baustoff-Checkboxen
baustoff_vals = sorted(gdf_pts["Baustoffklasse"].dropna().unique())
baustoff_options = [{"label": b, "value": b} for b in baustoff_vals]

# Straßenart-Checkboxen
road_vals = sorted(gdf_pts["StraßenartLabel"].dropna().unique())
road_options = [{"label": r, "value": r} for r in road_vals]

# --- Baujahr-Range (für Slider, ab 1900, Labels alle 25 Jahre) ---
BAUJAHR_MIN = 1900

if gdf_pts["Baujahr"].notna().any():
    BAUJAHR_MAX_DATA = int(gdf_pts["Baujahr"].max())
else:
    BAUJAHR_MAX_DATA = AGE_REF_YEAR

rest = (BAUJAHR_MAX_DATA - BAUJAHR_MIN) % 25
if rest != 0:
    BAUJAHR_MAX = BAUJAHR_MAX_DATA + (25 - rest)
else:
    BAUJAHR_MAX = BAUJAHR_MAX_DATA

baujahr_marks = {
    year: str(year)
    for year in range(BAUJAHR_MIN, BAUJAHR_MAX + 1, 25)
}

# Radio für Flächenanzeige: Zustandsnote / Traglastindex / Alter
choropleth_mode_options = [
    {"label": "Zustandsnote",       "value": "zustand"},
    {"label": "Traglastindex",      "value": "trag"},
    {"label": "Durchschnittsalter", "value": "alter"},
]


# --------------------------------------------------------------------
# 5) Hilfsfunktion: Figur bauen
# --------------------------------------------------------------------
def build_figure(selected_layers, selected_baustoff, selected_year_range, selected_road, choropleth_mode):
    fig = go.Figure()

    # 1) Deutschland-Umriss
    if "outline" in selected_layers:
        fig.add_trace(
            go.Choropleth(
                geojson=outline_json,
                locations=["germany_outline"],
                z=[0],
                featureidkey="properties.id",
                name="Deutschland-Umriss",
                showlegend=True,
                showscale=False,
                hoverinfo="skip",
                colorscale=[[0, "rgba(0,0,0,0)"], [1, "rgba(0,0,0,0)"]],
                marker_line_color="black",
                marker_line_width=2.0,
            )
        )

    # 2) Bundesländer
    if "states" in selected_layers:
        fig.add_trace(
            go.Choropleth(
                geojson=geojson_states,
                locations=gdf_states["state_id"],
                z=[0] * len(gdf_states),
                featureidkey="properties.state_id",
                name="Bundesländer",
                showlegend=True,
                showscale=False,
                hoverinfo="skip",
                colorscale=[[0, "rgba(0,0,0,0)"], [1, "rgba(0,0,0,0)"]],
                marker_line_color="rgba(0,0,0,0.6)",
                marker_line_width=1.0,
            )
        )

    # 3) Choropleth: Ø Zustandsnote / Ø Traglastindex / Ø Alter pro Landkreis
    if "choropleth" in selected_layers:
        if choropleth_mode == "trag":
            metric_col = "mean_trag"
            metric_label = "Ø Traglastindex"
        elif choropleth_mode == "alter":
            metric_col = "mean_age"
            metric_label = "Ø Alter (Jahre)"
        else:
            metric_col = "mean_zust"
            metric_label = "Ø Note"

        gplot_valid   = gplot[gplot[metric_col].notna()]
        gplot_missing = gplot[gplot[metric_col].isna()]

        # 3a) Kreise ohne Daten – hellgrau
        if len(gplot_missing) > 0:
            fig.add_trace(
                go.Choropleth(
                    geojson=geojson_kreise,
                    locations=gplot_missing["id"],
                    z=[0] * len(gplot_missing),
                    featureidkey="properties.id",
                    name="keine Daten",
                    showlegend=True,
                    showscale=False,
                    colorscale=[[0, "lightgrey"], [1, "lightgrey"]],
                    hoverinfo="skip",
                    marker_line_color="rgba(0,0,0,0)",
                    marker_line_width=0.0,
                )
            )

        # 3b) Kreise mit Daten – farbig
        if len(gplot_valid) > 0:
            fig.add_trace(
                go.Choropleth(
                    geojson=geojson_kreise,
                    locations=gplot_valid["id"],
                    z=gplot_valid[metric_col],
                    featureidkey="properties.id",
                    name=metric_label + " (Landkreise)",
                    showlegend=True,
                    showscale=True,
                    colorbar_title=metric_label,
                    colorscale="RdYlGn_r",
                    hovertemplate=f"<b>%{{text}}</b><br>{metric_label}: %{{z:.2f}}<extra></extra>",
                    text=gplot_valid["NAME"],
                    marker_line_color="rgba(0,0,0,0)",
                    marker_line_width=0.0,
                )
            )

    # 4) Landkreis-Grenzen
    if "kreise" in selected_layers:
        fig.add_trace(
            go.Choropleth(
                geojson=geojson_kreise,
                locations=gplot["id"],
                z=[0] * len(gplot),
                featureidkey="properties.id",
                name="Landkreis-Grenzen",
                showlegend=True,
                showscale=False,
                hoverinfo="skip",
                colorscale=[[0, "rgba(0,0,0,0)"], [1, "rgba(0,0,0,0)"]],
                marker_line_color="rgba(0,0,0,0.5)",
                marker_line_width=0.5,
            )
        )

    # 5) Brücken filtern (UND-Logik)
    pts = gdf_pts.copy()

    # Baustoffklasse
    if selected_baustoff:
        pts = pts[pts["Baustoffklasse"].isin(selected_baustoff)]

    # Baujahr-Range
    if (
        selected_year_range is not None
        and isinstance(selected_year_range, (list, tuple))
        and len(selected_year_range) == 2
    ):
        year_min, year_max = selected_year_range
        pts = pts[
            (pts["Baujahr"].notna()) &
            (pts["Baujahr"] >= year_min) &
            (pts["Baujahr"] <= year_max)
        ]

    # Straßenart
    if selected_road:
        pts = pts[pts["StraßenartLabel"].isin(selected_road)]

    # nur anzeigen, wenn es Punkte gibt
    if len(pts) > 0:
        fig.add_trace(
            go.Scattergeo(
                lon=pts["lon"],
                lat=pts["lat"],
                mode="markers",
                name="Brücken (gefiltert)",
                text=pts["hover"],
                hovertemplate="%{text}<extra></extra>",
                marker=dict(size=1.5, color="black", opacity=0.7),
                showlegend=True,
            )
        )

    # 6) Layout
    fig.update_geos(
        fitbounds="locations",
        visible=False,
        projection_type="mercator",
        center=dict(lat=51, lon=10),
        projection_scale=7,
    )

    fig.update_layout(
        margin={"r": 20, "t": 60, "l": 20, "b": 20},
        legend=dict(x=0.02, y=0.98, bgcolor="rgba(255,255,255,0.8)"),
        title=(
            "Mittlere Zustandsnote / Traglastindex / Alter Überbau pro Landkreis<br>"
            f"<sup>Zuordnung: {used_coords if spatial_join_ok else 'Name-Match'}</sup>"
        ),
    )

    return fig


# --------------------------------------------------------------------
# 6) Dash-App
# --------------------------------------------------------------------
app = dash.Dash(__name__)

app.layout = html.Div(
    style={"display": "flex", "height": "100vh", "fontFamily": "sans-serif"},
    children=[
        # linkes Menü
        html.Div(
            style={
                "width": "22%",
                "padding": "10px",
                "borderRight": "1px solid #ccc",
                "overflowY": "auto",
            },
            children=[
                html.H3("Ebenen"),
                dcc.Checklist(
                    id="layer-checklist",
                    options=layer_options,
                    value=[o["value"] for o in layer_options],  # alle an
                    labelStyle={"display": "block"},
                ),
                html.Hr(),
                html.H3("Flächenanzeige"),
                dcc.RadioItems(
                    id="choropleth-mode",
                    options=choropleth_mode_options,
                    value="zustand",  # Standard: Zustandsnote
                    labelStyle={"display": "block"},
                ),
                html.Hr(),
                html.H3("Baustoffklasse"),
                dcc.Checklist(
                    id="baustoff-checklist",
                    options=baustoff_options,
                    value=[],   # nichts gewählt = alle
                    labelStyle={"display": "block"},
                ),
                html.Hr(),
                html.H3("Baujahr Überbau"),
                dcc.RangeSlider(
                    id="year-slider",
                    min=BAUJAHR_MIN,
                    max=BAUJAHR_MAX,
                    step=1,
                    value=[BAUJAHR_MIN, BAUJAHR_MAX],
                    marks=baujahr_marks,     # Labels alle 25 Jahre ab 1900
                    allowCross=False,
                    tooltip={"always_visible": False, "placement": "bottom"},
                ),
                html.Hr(),
                html.H3("Straßenart"),
                dcc.Checklist(
                    id="road-checklist",
                    options=road_options,
                    value=[],
                    labelStyle={"display": "block"},
                ),
            ],
        ),

        # rechte Karte
        html.Div(
            style={"width": "78%", "padding": "10px"},
            children=[
                dcc.Graph(
                    id="map-figure",
                    style={"height": "100%"},
                )
            ],
        ),
    ],
)

@app.callback(
    Output("map-figure", "figure"),
    [
        Input("layer-checklist", "value"),
        Input("choropleth-mode", "value"),
        Input("baustoff-checklist", "value"),
        Input("year-slider", "value"),      # Baujahr-Range
        Input("road-checklist", "value"),
    ],
)
def update_map(selected_layers, choropleth_mode, selected_baustoff, selected_year_range, selected_road):
    if selected_layers is None:
        selected_layers = []
    if selected_baustoff is None:
        selected_baustoff = []
    if selected_year_range is None:
        selected_year_range = [BAUJAHR_MIN, BAUJAHR_MAX]
    if selected_road is None:
        selected_road = []
    if choropleth_mode is None:
        choropleth_mode = "zustand"
    return build_figure(
        selected_layers,
        selected_baustoff,
        selected_year_range,
        selected_road,
        choropleth_mode,
    )


if __name__ == "__main__":
    app.run(debug=True)
